# Analyse et Modélisation du Prix de l'Électricité - Danemark (DK1)
*Exploratory Data Analysis (EDA), Visualisations Avancées et Prédiction (LightGBM)*

---

## 1. Configuration et Chargement des Données

In [2]:
import urllib.request
import os
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import lightgbm as lgb
from sklearn.metrics import mean_squared_error
import shap
import statsmodels.api as sm
from statsmodels.tsa.seasonal import seasonal_decompose
import warnings

warnings.filterwarnings('ignore')

# --- Téléchargement ---
os.makedirs('../data/raw', exist_ok=True)
url = "https://data.open-power-system-data.org/time_series/latest/time_series_60min_singleindex.csv"
destination = "../data/raw/time_series_60min.csv"

if not os.path.exists(destination):
    print("⏳ Téléchargement du dataset...")
    try:
        urllib.request.urlretrieve(url, destination)
        print("✅ Dataset téléchargé !")
    except:
        print("⚠️ Impossible de télécharger, lecture directe depuis l'URL...")
        destination = url
else:
    print("✅ Dataset local trouvé.")

# --- Chargement ---
print("Lecture des données...")
df = pd.read_csv(destination, parse_dates=['utc_timestamp'], low_memory=False)
df = df.set_index('utc_timestamp')
print("Chargement terminé.")

c:\Users\gerau\Documents\Projet_spe1\.venv\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


✅ Dataset local trouvé.
Lecture des données...
Chargement terminé.


## 2. Préparation et Nettoyage (Zone DK1)

In [3]:
# Sélection des colonnes pour DK1 (Ouest Danemark)
cols_mapping = {
    'DK_1_price_day_ahead': 'price',
    'DK_1_load_actual_entsoe_transparency': 'load_actual',
    'DK_1_load_forecast_entsoe_transparency': 'load_forecast',
    'DK_1_solar_generation_actual': 'solar_generation',
    'DK_1_wind_generation_actual': 'wind_generation'
}

df_dk = df[list(cols_mapping.keys())].rename(columns=cols_mapping)

# --- Analyse de la Qualité (Choix de la période) ---
# On compte les données valides par an
yearly_counts = df_dk.groupby(df_dk.index.year).count()

fig = px.bar(
    yearly_counts, 
    barmode='group',
    title="Qualité des Données : Nombre d'observations valides par an",
    labels={"index": "Année", "value": "Heures valides", "variable": "Variable"},
    template="plotly_white"
)
fig.add_hline(y=8760, line_dash="dash", line_color="red", annotation_text="Année Complète")
fig.show()



In [4]:
# -> Décision : On garde 2018-2019 car ce sont les années complètes et récentes
df_dk = df_dk.loc['2018-01-01':'2019-12-31']
df_dk = df_dk.interpolate(method='linear').dropna()

print(f"Données filtrées (2018-2019) : {df_dk.shape[0]} heures.")

Données filtrées (2018-2019) : 17520 heures.


In [5]:
# Affichage des pourcentages de remplissage pour validation numérique
full_year_hours = 8760
completeness_pct = (yearly_counts / full_year_hours * 100).round(1)
print("Pourcentage de données disponibles par année (basé sur 8760h) :")
display(completeness_pct.style.background_gradient(cmap='RdYlGn', vmin=90, vmax=100))

Pourcentage de données disponibles par année (basé sur 8760h) :


## 3. Feature Engineering (Variables Temporelles)

In [6]:
# Ajout des informations calendaires
df_dk['hour'] = df_dk.index.hour
df_dk['day_of_week'] = df_dk.index.dayofweek
df_dk['day_name'] = df_dk.index.day_name()
df_dk['month'] = df_dk.index.month
df_dk['month_name'] = df_dk.index.month_name()

# Saisons
def get_season(month):
    if month in [12, 1, 2]: return 'Hiver'
    elif month in [3, 4, 5]: return 'Printemps'
    elif month in [6, 7, 8]: return 'Été'
    else: return 'Automne'
df_dk['season'] = df_dk['month'].apply(get_season)

# Week-end vs Semaine
df_dk['day_type'] = df_dk['day_of_week'].apply(lambda x: 'Week-end' if x >= 5 else 'Semaine')

display(df_dk.head())

price  load_actual  load_forecast  \
utc_timestamp                                                  
2018-01-01 00:00:00+00:00  26.43      1741.92         1747.8   
2018-01-01 01:00:00+00:00  26.10      1657.52         1659.4   
2018-01-01 02:00:00+00:00  24.70      1594.26         1599.5   
2018-01-01 03:00:00+00:00  24.74      1535.88         1560.5   
2018-01-01 04:00:00+00:00  18.01      1505.07         1534.0   

                           solar_generation  wind_generation  hour  \
utc_timestamp                                                        
2018-01-01 00:00:00+00:00               0.0          1849.85     0   
2018-01-01 01:00:00+00:00               0.0          1609.74     1   
2018-01-01 02:00:00+00:00               0.0          1606.32     2   
2018-01-01 03:00:00+00:00               0.0          1612.06     3   
2018-01-01 04:00:00+00:00               0.0          1617.73     4   

                           day_of_week day_name  month month_name season  \
utc_timestamp                                                              
2018-01-01 00:00:00+00:00            0   Monday      1    January  Hiver   
2018-01-01 01:00:00+00:00            0   Monday      1    January  Hiver   
2018-01-01 02:00:00+00:00            0   Monday      1    January  Hiver   
2018-01-01 03:00:00+00:00            0   Monday      1    January  Hiver   
2018-01-01 04:00:00+00:00            0   Monday      1    January  Hiver   

                          day_type  
utc_timestamp                       
2018-01-01 00:00:00+00:00  Semaine  
2018-01-01 01:00:00+00:00  Semaine  
2018-01-01 02:00:00+00:00  Semaine  
2018-01-01 03:00:00+00:00  Semaine  
2018-01-01 04:00:00+00:00  Semaine

## 4. Analyse Statistique Globale

In [7]:
# 1. Tableau de KPI
desc = df_dk['price'].describe()
nb_neg = df_dk[df_dk['price'] < 0].shape[0]
pct_neg = (nb_neg / len(df_dk)) * 100

stats_df = pd.DataFrame({
    'KPI': ['Prix Moyen', 'Médiane', 'Max', 'Min', 'Volatilité (Std)', 'Heures Négatives', '% Temps Négatif'],
    'Valeur': [
        f"{desc['mean']:.2f} €", f"{desc['50%']:.2f} €", f"{desc['max']:.2f} €", 
        f"{desc['min']:.2f} €", f"{desc['std']:.2f}", f"{nb_neg} h", f"{pct_neg:.2f} %"
    ]
})
display(stats_df)

KPI    Valeur
0        Prix Moyen   41.27 €
1           Médiane   41.20 €
2               Max  144.33 €
3               Min  -48.29 €
4  Volatilité (Std)     14.41
5  Heures Négatives     183 h
6   % Temps Négatif    1.04 %

## 5. Analyse Temporelle (Cycles & Saisonnalité)

In [8]:
# A. Saisonnalité (Boxplots par Mois)
months_order = ["January", "February", "March", "April", "May", "June", 
                "July", "August", "September", "October", "November", "December"]
fig = px.box(
    df_dk, x="month_name", y="price", color="season",
    category_orders={"month_name": months_order},
    title="Saisonnalité : Distribution des Prix par Mois",
    template="plotly_white"
)
fig.show()



In [9]:
# B. Heatmap Hebdomadaire (Le rythme de la semaine)
heatmap_data = df_dk.groupby(['day_name', 'hour'])['price'].mean().reset_index()
days_order = ["Monday", "Tuesday", "Wednesday", "Thursday", "Friday", "Saturday", "Sunday"]

fig = px.imshow(
    heatmap_data.pivot(index='day_name', columns='hour', values='price').reindex(days_order),
    title="Heatmap : Profil Hebdomadaire des Prix",
    color_continuous_scale="RdYlGn_r", aspect="auto"
)
fig.show()



In [10]:
# C. Impact Week-end vs Semaine (Profil Horaire)
weekend_hourly = df_dk.groupby(['day_type', 'hour'])['price'].mean().reset_index()
fig = px.line(
    weekend_hourly, x="hour", y="price", color="day_type",
    title="Comparaison Semaine vs Week-end (Profil Horaire)",
    color_discrete_map={"Semaine": "royalblue", "Week-end": "orange"},
    template="plotly_white"
)
fig.show()



In [11]:
# D. Saisonnalité Annuelle : Distribution Mensuelle ---
fig1 = px.box(
    df_dk, 
    x="month_name", 
    y="price", 
    color="month_name",
    category_orders={"month_name": months_order}, # Force l'ordre Jan -> Déc
    title="Saisonnalité Annuelle : Distribution des Prix par Mois",
    labels={"price": "Prix (€/MWh)", "month_name": "Mois"},
    template="plotly_white"
)
fig1.update_layout(showlegend=False) # Pas besoin de légende, l'axe X suffit
fig1.show()

In [12]:
# E. Saisonnalité Hebdomadaire : Distribution par Jour ---
fig2 = px.box(
    df_dk, 
    x="day_name", 
    y="price", 
    color="day_name",
    category_orders={"day_name": days_order}, # Force l'ordre Lun -> Dim
    title="Saisonnalité Hebdomadaire : Distribution par Jour",
    labels={"price": "Prix (€/MWh)", "day_name": "Jour"},
    template="plotly_white"
)
fig2.update_layout(showlegend=False)
fig2.show()

In [13]:
# F. Saisonnalité Quotidienne : Distribution par Heure ---
fig3 = px.box(
    df_dk, 
    x="hour", 
    y="price", 
    title="3. Saisonnalité Quotidienne : Profil Horaire (Distribution)",
    labels={"price": "Prix (€/MWh)", "hour": "Heure de la journée"},
    template="plotly_white",
    color_discrete_sequence=["#1e66b8"] 
)
fig3.show()

In [14]:
# G. Comparatif Semaine vs Week-end ---
# On compare les distributions globales
fig4 = px.box(
    df_dk, 
    x="day_type", 
    y="price", 
    color="day_type",
    title="4. Semaine vs Week-end : Impact sur les Prix",
    labels={"price": "Prix (€/MWh)", "day_type": "Type de Jour"},
    template="plotly_white",
    color_discrete_map={"Semaine": "royalblue", "Week-end": "orange"}
)
fig4.show()

In [15]:
# H. Analyse par Saison ---

# --- 1. Création de la variable 'Saison' ---
def get_season(month):
    if month in [12, 1, 2]:
        return 'Hiver'
    elif month in [3, 4, 5]:
        return 'Printemps'
    elif month in [6, 7, 8]:
        return 'Été'
    else:
        return 'Automne'

# On applique la fonction sur le mois de l'index
df_dk['season'] = df_dk.index.month.map(get_season)

# Ordre logique pour l'affichage (sinon ce sera alphabétique)
season_order = ["Hiver", "Printemps", "Été", "Automne"]

# --- 2. Graphique A : Distribution des Prix par Saison ---
fig_box = px.box(
    df_dk, 
    x="season", 
    y="price", 
    color="season",
    category_orders={"season": season_order},
    title="Distribution des Prix par Saison (DK1)",
    labels={"price": "Prix (€/MWh)", "season": "Saison"},
    template="plotly_white"
)
fig_box.show()

# --- 3. Graphique B : Profil Horaire Moyen par Saison ---
# On calcule le prix moyen par saison et par heure
season_hourly = df_dk.groupby(['season', 'hour'])['price'].mean().reset_index()

fig_line = px.line(
    season_hourly, 
    x="hour", 
    y="price", 
    color="season",
    category_orders={"season": season_order},
    title="Profil Horaire Moyen selon la Saison",
    labels={"price": "Prix Moyen (€/MWh)", "hour": "Heure de la journée"},
    template="plotly_white"
)
# Ajout de points pour bien voir les heures
fig_line.update_traces(mode='lines+markers')
fig_line.show()

In [16]:
# I. Décomposition STL (Tendance vs Saisonnalité)
# Zoom sur Janvier 2019 pour y voir clair
sample = df_dk.loc['2019-01-01':'2019-01-31']
res = seasonal_decompose(sample['price'], period=24)

# Création des sous-graphiques avec titres en Français
fig = make_subplots(
    rows=4, cols=1, 
    shared_xaxes=True, 
    subplot_titles=("Observé (Prix Réel)", "Tendance de fond", "Saisonnalité (24h)", "Résidus (Bruit)")
)

# Ajout des traces (courbes)
fig.add_trace(go.Scatter(x=sample.index, y=res.observed, name='Observé'), row=1, col=1)
fig.add_trace(go.Scatter(x=sample.index, y=res.trend, name='Tendance', line_color='red'), row=2, col=1)
fig.add_trace(go.Scatter(x=sample.index, y=res.seasonal, name='Saisonnalité', line_color='green'), row=3, col=1)
fig.add_trace(go.Scatter(x=sample.index, y=res.resid, name='Résidus', mode='markers', marker_size=3), row=4, col=1)

# Mise en page
fig.update_layout(height=800, title="Décomposition STL (Janvier 2019)", showlegend=False)
fig.show()

## 6. Analyse Physique (Marché & Fondamentaux)

In [17]:
# A. Matrice de Corrélation
corr = df_dk[['price', 'load_actual', 'wind_generation', 'solar_generation']].corr()
fig = px.imshow(corr, text_auto=".2f", title="Matrice de Corrélation", color_continuous_scale="RdBu_r", aspect="auto")
fig.show()



In [18]:
# B. Scatter Plot : Vent vs Prix (Effet Cannibale)
fig = px.scatter(
    df_dk.sample(5000), x="wind_generation", y="price", color="load_actual",
    title="Effet Cannibale : Le Vent écrase les Prix",
    trendline="lowess", trendline_color_override="green",
    opacity=0.5, template="plotly_white"
)
fig.show()



In [19]:
# C. Price Duration Curve
sorted_price = df_dk['price'].sort_values(ascending=False).reset_index(drop=True)
sorted_price.index = (sorted_price.index / len(sorted_price)) * 100
fig = px.area(
    x=sorted_price.index, y=sorted_price.values,
    title="Price Duration Curve (Volatilité)",
    labels={"x": "% du temps", "y": "Prix (€/MWh)"},
    template="plotly_white"
)
fig.add_hline(y=0, line_dash="dash", line_color="red")
fig.show()

In [20]:
# D. L'Effet du Vent sur les Prix (Scatter Plot)
# Insight : Observez la corrélation inverse. Quand le vent dépasse 2000-3000 MW, les prix s'effondrent.
fig = px.scatter(
    df_dk.sample(5000), # Échantillon pour alléger le rendu
    x="wind_generation", 
    y="price", 
    color="load_actual",
    title="Corrélation : Production Éolienne vs Prix (DK1)",
    labels={"wind_generation": "Production Éolienne (MW)", "price": "Prix (€/MWh)", "load_actual": "Demande (MW)"},
    template="plotly_white",
    opacity=0.6,
    trendline="lowess" # Ligne de tendance locale
)
fig.update_layout(height=600)
fig.show()

In [21]:
# --- E. Analyse des Prix Négatifs (Fréquence Mensuelle) ---
# Insight : Quand les prix négatifs surviennent-ils le plus souvent ?
neg_df = df_dk[df_dk['price'] < 0].copy()
# Ajouter une colonne 'year' basée sur l'index datetime (il n'y a pas de colonne 'year' dans df_dk)
neg_df['year'] = neg_df.index.year
# 'month' existe déjà mais on peut la recalculer pour être sûr
neg_df['month'] = neg_df.index.month

negative_prices = neg_df.groupby(['year', 'month']).size().reset_index(name='count')

# Création d'une date fictive pour l'axe X
negative_prices['date'] = pd.to_datetime(negative_prices[['year', 'month']].assign(DAY=1))

fig = px.bar(
    negative_prices,
    x='date',
    y='count',
    title="Fréquence des Prix Négatifs (Nombre d'heures par mois)",
    labels={'count': "Nombre d'heures < 0€", 'date': 'Date'},
    color='count',
    color_continuous_scale='Reds'
)
fig.show()

## 7. Modélisation Prédictive (LightGBM)

In [22]:
# 1. Préparation pour le ML (Lags)
df_ml = df_dk.copy()
df_ml['price_lag_24h'] = df_ml['price'].shift(24)
df_ml['wind_forecast_lag_24h'] = df_ml['wind_generation'].shift(24)
df_ml = df_ml.dropna()

features = ['hour', 'day_of_week', 'month', 'price_lag_24h', 'load_forecast', 'wind_forecast_lag_24h', 'solar_generation']
target = 'price'

# Split Train/Test (Juin 2019)
split_date = '2019-06-01'
X_train = df_ml.loc[df_ml.index < split_date, features]
y_train = df_ml.loc[df_ml.index < split_date, target]
X_test = df_ml.loc[df_ml.index >= split_date, features]
y_test = df_ml.loc[df_ml.index >= split_date, target]



In [23]:
# 2. Entraînement
print("Entraînement LightGBM...")
model = lgb.LGBMRegressor(n_estimators=500, random_state=42, verbose=-1)
model.fit(X_train, y_train)
y_pred = model.predict(X_test)

rmse = np.sqrt(mean_squared_error(y_test, y_pred))
print(f"RMSE Test : {rmse:.2f} €/MWh")



Entraînement LightGBM...
RMSE Test : 11.61 €/MWh


In [24]:
# 3. Visualisation Interactive (Réel vs Prédiction)
fig = go.Figure()
fig.add_trace(go.Scatter(x=y_test.index, y=y_test.values, name='Réel', line=dict(color='royalblue', width=1.5)))
fig.add_trace(go.Scatter(x=y_test.index, y=y_pred, name='Prédiction', line=dict(color='firebrick', dash='dot', width=1.5)))
fig.update_layout(
    title="Prédiction vs Réalité (Avec Zoom)", 
    xaxis_title="Date", yaxis_title="Prix",
    template="plotly_white"
)
fig.update_xaxes(rangeslider_visible=True)
# Zoom initial sur 2 semaines
fig.update_xaxes(range=[y_test.index[0], y_test.index[336]])
fig.show()



In [25]:
# 4. Feature Importance (SHAP)
explainer = shap.TreeExplainer(model)
shap_values = explainer.shap_values(X_test)
shap_sum = np.abs(shap_values).mean(axis=0)
imp_df = pd.DataFrame({'feature': features, 'importance': shap_sum}).sort_values('importance', ascending=True)

fig = px.bar(imp_df, x='importance', y='feature', orientation='h', title="Importance des Variables (SHAP)", template="plotly_white")
fig.show()